In [1]:
import numpy as np
import pandas as pd
import glob, pdb, os

In [2]:
study_data_path = '../IntentData/Python_data/'
javascript_path = "../IntentData/Javascript_data/"
javascript_files = ["commands_data", "key_data", "selection_data", "toolbar_data"]
sum_subj = 17 # Ignore subj 0: "16 participants" in the paper

# Map 7 formatting rules to 7 labels
label_index = dict()
label_index["['', 'Title:', 'Alignment', 'Center', 'and', 'Underline\\n', 'Subtitle:', 'Underline\\n', 'Paragraph:', '1', 'Indent']"] = 0
label_index["['', 'Title:', 'Size', 'Big', 'and', 'Underline\\n', 'Subtitle:', 'Underline\\n', 'Paragraph:', 'Alignment', 'Right']"] = 1
label_index["['', 'Title:', 'Bold', 'and', 'Underline\\n', 'Subtitle:', 'Bold\\n', 'Paragraph:', '1', 'Indent']"] = 2
label_index["['', 'Title:', '1', 'Indent', 'and', 'Italic\\n', 'Subtitle:', '1', 'Indent\\n', 'Paragraph:', 'Font', 'Family', 'Consolas']"] = 3
label_index["['', 'Title:', 'Size', 'Big', 'and', 'Bold\\n', 'Subtitle:', 'Bold\\n', 'Paragraph:', 'Italic']"] = 4
label_index["['', 'Title:', 'Size', 'Big\\n', 'Subtitle:', 'Bold\\n', 'Paragraph:', 'Font', 'Family', 'Consolas']"] = 5
label_index["['', 'Title:', 'Font', 'Family', 'Consolas', 'and', 'Alignment', 'Center\\n', 'Subtitle:', 'Font', 'Family', 'Consolas\\n', 'Paragraph:', 'Italic']"] = 6
# 7 formatting rules
formatting_rule = list()
formatting_rule.append({'Title': ['Alignment', 'Center', 'and', 'Underline'], 'Subtitle': ['Underline'], 'Paragraph': ['1', 'Indent']})
formatting_rule.append({'Title': ['Size', 'Big', 'and', 'Underline'], 'Subtitle': ['Underline'], 'Paragraph': ['Alignment', 'Right']})
formatting_rule.append({'Title': ['Bold', 'and', 'Underline'], 'Subtitle': ['Bold'], 'Paragraph': ['1', 'Indent']})
formatting_rule.append({'Title': ['1', 'Indent', 'and', 'Italic'], 'Subtitle': ['1', 'Indent'], 'Paragraph': ['Font', 'Family', 'Consolas']})
formatting_rule.append({'Title': ['Size', 'Big', 'and', 'Bold'], 'Subtitle': ['Bold'], 'Paragraph': ['Italic']})
formatting_rule.append({'Title': ['Size', 'Big'], 'Subtitle': ['Bold'], 'Paragraph': ['Font', 'Family', 'Consolas']})
formatting_rule.append({'Title': ['Font', 'Family', 'Consolas', 'and', 'Alignment', 'Center'], 'Subtitle': ['Font', 'Family', 'Consolas'], 'Paragraph': ['Italic']})
formatting_rule

[{'Title': ['Alignment', 'Center', 'and', 'Underline'],
  'Subtitle': ['Underline'],
  'Paragraph': ['1', 'Indent']},
 {'Title': ['Size', 'Big', 'and', 'Underline'],
  'Subtitle': ['Underline'],
  'Paragraph': ['Alignment', 'Right']},
 {'Title': ['Bold', 'and', 'Underline'],
  'Subtitle': ['Bold'],
  'Paragraph': ['1', 'Indent']},
 {'Title': ['1', 'Indent', 'and', 'Italic'],
  'Subtitle': ['1', 'Indent'],
  'Paragraph': ['Font', 'Family', 'Consolas']},
 {'Title': ['Size', 'Big', 'and', 'Bold'],
  'Subtitle': ['Bold'],
  'Paragraph': ['Italic']},
 {'Title': ['Size', 'Big'],
  'Subtitle': ['Bold'],
  'Paragraph': ['Font', 'Family', 'Consolas']},
 {'Title': ['Font', 'Family', 'Consolas', 'and', 'Alignment', 'Center'],
  'Subtitle': ['Font', 'Family', 'Consolas'],
  'Paragraph': ['Italic']}]

In [3]:
def cleanEye(df, DISPLAY_X= 2560, DISPLAY_Y=1600):
    df.fillna(0, inplace=True)
    # Only keep samples where 0<X<1 and 0<Y<1
    df = df[(df['Left_Gaze_X'] > 0.0) & (df['Right_Gaze_X'] > 0.0) & (df['Left_Gaze_X'] < 1.0) & (df['Right_Gaze_X'] < 1.0) 
        & (df['Left_Gaze_Y'] > 0.0) & (df['Right_Gaze_Y'] > 0.0) & (df['Left_Gaze_Y'] < 1.0) & (df['Right_Gaze_Y'] < 1.0)]
    # Mean(Left_Gaze_XorY,Right_Gaze_XorY)*DISPLAY_XorY
    df.loc[:, "Gaze_X"] = (df.loc[:, 'Left_Gaze_X'] + df.loc[:, 'Right_Gaze_X'])/2 * DISPLAY_X
    df.loc[:, "Gaze_Y"] = (df.loc[:, 'Left_Gaze_Y'] + df.loc[:, 'Right_Gaze_Y'])/2 * DISPLAY_Y
    df = df.reset_index()
    return df

In [4]:
def filter_start_end(data, df_starts, df_ends):
    # Only keep data in the time segment
    new_data = pd.DataFrame()
    for start, end, condition, part, taskID in zip(df_starts.Timestamp, df_ends.Timestamp, df_starts.condition, df_starts.part, df_starts.taskID):
        # use iloc here
        tmp = data[ (data.Timestamp >= start) & (data.Timestamp <= end) ]
        tmp["condition"] = condition
        tmp["part"] = part
        tmp["taskID"] = taskID
        new_data = new_data.append(tmp)
    return new_data

In [5]:
if os.path.exists("../ReRun/filtered_data.pkl"):
    result = pd.read_pickle("../ReRun/filtered_data.pkl")
else:
    result = None
    for subj in range(1,sum_subj):
        print("subj:",subj)
        procedure_file = glob.glob(study_data_path+"procedure_%d_*.csv"%(subj))
        lorem_file = glob.glob(study_data_path+"lorem_text_%d_*.csv"%(subj))
        eye_file = glob.glob(study_data_path+"eyedata_%d_*.csv"%(subj))
        mouse_pos_file = glob.glob(study_data_path+"mouse_pos_%d_*.csv"%(subj))
        mouse_click_file = glob.glob(study_data_path+"mouse_click_%d_*.csv"%(subj))

        # Actually none of them contains multiple csv files
        assert len(procedure_file)==1
        assert len(lorem_file)==1
        assert len(eye_file)==1
        assert len(mouse_pos_file)==1
        assert len(mouse_click_file)==1

        # Load dataframe from .csv
        df_p = pd.read_csv(procedure_file[-1])
        df_l = pd.read_csv(lorem_file[-1])
        df_e = pd.read_csv(eye_file[-1])
        df_mouse_pos = pd.read_csv(mouse_pos_file[-1])
        df_mouse_click = pd.read_csv(mouse_click_file[-1])

        ''''print("df_p:",df_p)
        print("df_l:",df_l)
        print("df_e:",df_e)
        print("df_mouse_pos:",df_mouse_pos)
        print("df_mouse_click:",df_mouse_click)'''

        # Calculate timestamp
        #print("df_p.Timestamp BEF:",df_p.Timestamp)
        df_p.Timestamp = (df_p.Timestamp * 1000).astype(int)
        df_l.Timestamp = (df_l.Timestamp * 1000).astype(int)
        df_e.Timestamp = (df_e.Timestamp * 1000).astype(int)
        df_mouse_pos.Timestamp = (df_mouse_pos.Timestamp * 1000).astype(int)
        df_mouse_click.Timestamp = (df_mouse_click.Timestamp * 1000).astype(int)
        #print("df_p.Timestamp AFT:",df_p.Timestamp)

        # ??? For lorem_text and procedure, only take data where condition==1
        df_l_1 = df_l[df_l.condition == 1]
        df_p_1 = df_p[df_p.condition == 1]
        ''''print("df_l_1:\n",df_l_1)
        print("df_p_1:\n",df_p_1)'''

        # Start-End-Filter (condition 1)
        ## ????? WHY?
        df_starts = df_l_1[(df_l_1.isCurrentlyPasting == False) & (df_l_1.isStudy == True)]
        #print("df_starts:\n",df_starts)
        ## Only keep PID, Timestamp, condition, part and taskID
        df_starts = df_starts.drop(["isCurrentlyPasting", "isStudy", "lorem_format", "lorem_text", "rules"], axis = 1)
        #print("df_starts:\n",df_starts)

        ## ????? WHY?
        df_ends = df_p_1[(df_p_1.isEscapePressed == True) & (df_p_1.isStudy == True) & (df_p_1.isOverlayDisplayed == False)]
        #print("df_ends:\n",df_ends)
        ## Only keep PID, Timestamp, condition, part and taskID(can be -1??????)
        df_ends = df_ends.drop(["isEscapePressed", "isStudy", "isOverlayDisplayed"], axis = 1)
        #print("df_ends:\n",df_ends)

        ## Add a new column of ID starting from 0 consecutively
        df_starts = df_starts.reset_index()
        df_ends = df_ends.reset_index()
        ''''print("df_starts:\n",df_starts)
        print("df_ends:\n",df_ends)'''

        # Get integer labels (0~6) from formatting rule strings
        labels = pd.DataFrame(df_l_1[(df_l_1.rules != "None") & (df_l_1.isStudy == True)].rules)
        labels = labels.apply(lambda x: label_index[x[0]], axis=1)
        #print("labels:\n",labels)

        # Read javascript files
        unfiltered_data = pd.DataFrame()
        for javascript_file in javascript_files:
            file = glob.glob(javascript_path + javascript_file + "_%d.csv"%(subj))
            assert len(file)==1
            data = pd.read_csv(file[-1])
            print(file[-1])
            ''''for key in data.keys():
                if key=='Timestamp':
                    continue
                print(key, pd.unique(data[key]))'''
            # Remove first empty line done by lizard
            data = data.iloc[1:]
            # Add two columns: type = "commands"/"key"/"selection"/"toolbar"; PID = subj
            data['type'] = javascript_file.replace("_data", "")
            data['PID'] = subj
            # Concatenate to "unfiltered_data"
            unfiltered_data = pd.concat([unfiltered_data, data], sort=False)

        # Add two columns to eye data
        df_e['type'] = "eye"
        df_e['PID'] = subj
        # Remove invalid data and convert from (0,1) to real pixels
        df_e = cleanEye(df_e)

        unfiltered_data = pd.concat([unfiltered_data, df_e], sort=False)
        df_mouse_pos["type"] = "pos"
        unfiltered_data = pd.concat([unfiltered_data, df_mouse_pos], sort=False)
        df_mouse_click["type"] = "click"
        unfiltered_data = pd.concat([unfiltered_data, df_mouse_click], sort=False)

        # filter according to rulesets
        ## add 300ms to prevent pasting to be included??????
        df_starts.Timestamp += 300
        ## Only keep the data inside the time segments
        filtered_data = filter_start_end(unfiltered_data, df_starts, df_ends)
        df_starts['type'] = "start"
        df_starts = df_starts.drop(["index"], axis = 1)
        filtered_data = pd.concat([filtered_data, df_starts], sort=False)

        df_ends['type'] = "end"
        df_ends.taskID = df_ends.taskID.replace(-1, 7)
        df_ends.taskID -= 1
        df_ends = df_ends.drop(["index"], axis = 1)
        filtered_data = pd.concat([filtered_data, df_ends], sort=False)

        df_l_1['type'] = "lorem"
        filtered_data = pd.concat([filtered_data, df_l_1], sort=False)

        # remove tutorial part
        filtered_data = filtered_data[(filtered_data.part != 0)]

        # add labels???????
        filtered_data["label"] = filtered_data.apply(lambda x: labels.iloc[[(7 * (x.part - 1)) + x.taskID]].values[0], axis=1)

        # convert rules back to list
        #filtered_data["rules"] = filtered_data["rules"].apply(lambda x: x.strip('][').split(', ')[1:] if isinstance(x, str) else None)
        # this one overwrites everything, based on labels
        filtered_data["rules"] = filtered_data["label"].apply(lambda x: formatting_rule[x])

        filtered_data = filtered_data.drop(["isStudy"], axis = 1).reset_index()

        # combine for all participants
        #pdb.set_trace()
        if result is None:
            result = filtered_data
        else:
            result = pd.concat([result, filtered_data], sort=False)

    result.to_pickle("../ReRun/filtered_data.pkl")
print(result)

        level_0      Timestamp   event      type  PID  key data range  index  \
0            19  1575388379768     Tab  commands    1  NaN  NaN   NaN    NaN   
1            20  1575388384967  Ctrl+I  commands    1  NaN  NaN   NaN    NaN   
2            21  1575388388830     Tab  commands    1  NaN  NaN   NaN    NaN   
3            22  1575388390782  Ctrl+Z  commands    1  NaN  NaN   NaN    NaN   
4            23  1575388395487     Tab  commands    1  NaN  NaN   NaN    NaN   
...         ...            ...     ...       ...  ...  ...  ...   ...    ...   
683124       69  1603897372746     NaN     lorem   16  NaN  NaN   NaN    NaN   
683125       70  1603897429608     NaN     lorem   16  NaN  NaN   NaN    NaN   
683126       71  1603897429849     NaN     lorem   16  NaN  NaN   NaN    NaN   
683127       72  1603897491765     NaN     lorem   16  NaN  NaN   NaN    NaN   
683128       73  1603897492016     NaN     lorem   16  NaN  NaN   NaN    NaN   

        Left_Gaze_X  ...  clientY  cond

## Compare the generated and saved filtered_data

In [2]:
# Check if the result here is the same as that saved by Jan
result = pd.read_pickle("../ReRun/filtered_data.pkl")
pre_result = pd.read_pickle("../IntentData/Preprocessing_data/filtered_data.pkl")

result.fillna(0, inplace=True)
pre_result.fillna(0, inplace=True)

idx = np.where(pre_result!=result)
idx

(array([     139,      139,      139, ..., 10116492, 10116493, 10116494]),
 array([10, 12, 16, ..., 16, 10,  9]))

In [37]:
# columns that can be different
print(np.unique(idx[1]))
result.columns[np.unique(idx[1])]
np.where(idx[1]==1)[0]
print(pre_result.iloc[idx[0][np.where(idx[1]==1)[0]],idx[1][np.where(idx[1]==1)[0]]],result.iloc[idx[0][np.where(idx[1]==1)[0]],idx[1][np.where(idx[1]==1)[0]]])

[ 1  9 10 11 12 15 16]
            Timestamp      Timestamp      Timestamp      Timestamp  \
9805    1575388411623  1575388411623  1575388411623  1575388411623   
56789   1575388567787  1575388567787  1575388567787  1575388567787   
69831   1575388607232  1575388607232  1575388607232  1575388607232   
72534   1575388616827  1575388616827  1575388616827  1575388616827   
78669   1575388639022  1575388639022  1575388639022  1575388639022   
...               ...            ...            ...            ...   
635390  1603897392982  1603897392982  1603897392982  1603897392982   
648780  1603897436218  1603897436218  1603897436218  1603897436218   
660707  1603897478712  1603897478712  1603897478712  1603897478712   
661641  1603897482847  1603897482847  1603897482847  1603897482847   
672132  1603897511607  1603897511607  1603897511607  1603897511607   

            Timestamp      Timestamp      Timestamp      Timestamp  \
9805    1575388411623  1575388411623  1575388411623  1575388411623

In [24]:
for idxx in np.unique(idx[0]).tolist():
    print(pre_result.iloc[idx[0][np.where(idx[0]==idxx)[0]],idx[1][np.where(idx[0]==idxx)[0]]]-result.iloc[idx[0][np.where(idx[0]==idxx)[0]],idx[1][np.where(idx[0]==idxx)[0]]])
    #pdb.set_trace()
#pd.concat([result,pre_result]).drop_duplicates(keep=False)

      Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
139  5.551115e-17  5.551115e-17  1.136868e-13
139  5.551115e-17  5.551115e-17  1.136868e-13
139  5.551115e-17  5.551115e-17  1.136868e-13
      Left_Gaze_Y
140  5.551115e-17
      Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
141  1.110223e-16  5.551115e-17  1.136868e-13
141  1.110223e-16  5.551115e-17  1.136868e-13
141  1.110223e-16  5.551115e-17  1.136868e-13
      Left_Gaze_Y  Right_Gaze_X        Gaze_Y
142  2.775558e-17  1.110223e-16  5.684342e-14
142  2.775558e-17  1.110223e-16  5.684342e-14
142  2.775558e-17  1.110223e-16  5.684342e-14
      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_X        Gaze_X        Gaze_Y
144  1.110223e-16  5.551115e-17  1.110223e-16  4.547474e-13  5.684342e-14
144  1.110223e-16  5.551115e-17  1.110223e-16  4.547474e-13  5.684342e-14
144  1.110223e-16  5.551115e-17  1.110223e-16  4.547474e-13  5.684342e-14
144  1.110223e-16  5.551115e-17  1.110223e-16  4.547474e-13  5.684342e-14
144  1.110223e-16  5.551115e-17  1.110223e

      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_X  Right_Gaze_Y        Gaze_Y
184 -5.551115e-17  2.775558e-17  5.551115e-17  5.551115e-17  1.136868e-13
184 -5.551115e-17  2.775558e-17  5.551115e-17  5.551115e-17  1.136868e-13
184 -5.551115e-17  2.775558e-17  5.551115e-17  5.551115e-17  1.136868e-13
184 -5.551115e-17  2.775558e-17  5.551115e-17  5.551115e-17  1.136868e-13
184 -5.551115e-17  2.775558e-17  5.551115e-17  5.551115e-17  1.136868e-13
      Left_Gaze_Y        Gaze_Y
185  5.551115e-17  5.684342e-14
185  5.551115e-17  5.684342e-14
      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_X  Right_Gaze_Y        Gaze_X  \
186  5.551115e-17  5.551115e-17  1.110223e-16  2.775558e-17  2.273737e-13   
186  5.551115e-17  5.551115e-17  1.110223e-16  2.775558e-17  2.273737e-13   
186  5.551115e-17  5.551115e-17  1.110223e-16  2.775558e-17  2.273737e-13   
186  5.551115e-17  5.551115e-17  1.110223e-16  2.775558e-17  2.273737e-13   
186  5.551115e-17  5.551115e-17  1.110223e-16  2.775558e-17  2.273737e-13  

      Left_Gaze_Y  Right_Gaze_X  Right_Gaze_Y        Gaze_X        Gaze_Y
218  5.551115e-17  1.110223e-16  2.775558e-17  2.273737e-13  1.136868e-13
218  5.551115e-17  1.110223e-16  2.775558e-17  2.273737e-13  1.136868e-13
218  5.551115e-17  1.110223e-16  2.775558e-17  2.273737e-13  1.136868e-13
218  5.551115e-17  1.110223e-16  2.775558e-17  2.273737e-13  1.136868e-13
218  5.551115e-17  1.110223e-16  2.775558e-17  2.273737e-13  1.136868e-13
      Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
219  5.551115e-17  5.551115e-17  1.136868e-13
219  5.551115e-17  5.551115e-17  1.136868e-13
219  5.551115e-17  5.551115e-17  1.136868e-13
      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_X        Gaze_X
220  5.551115e-17  2.775558e-17  1.110223e-16  2.273737e-13
220  5.551115e-17  2.775558e-17  1.110223e-16  2.273737e-13
220  5.551115e-17  2.775558e-17  1.110223e-16  2.273737e-13
220  5.551115e-17  2.775558e-17  1.110223e-16  2.273737e-13
      Left_Gaze_X   Left_Gaze_Y        Gaze_Y
222 -5.551115e-17  2.77555

      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_X  Right_Gaze_Y        Gaze_X  \
252  1.110223e-16  5.551115e-17  1.110223e-16  2.775558e-17  4.547474e-13   
252  1.110223e-16  5.551115e-17  1.110223e-16  2.775558e-17  4.547474e-13   
252  1.110223e-16  5.551115e-17  1.110223e-16  2.775558e-17  4.547474e-13   
252  1.110223e-16  5.551115e-17  1.110223e-16  2.775558e-17  4.547474e-13   
252  1.110223e-16  5.551115e-17  1.110223e-16  2.775558e-17  4.547474e-13   
252  1.110223e-16  5.551115e-17  1.110223e-16  2.775558e-17  4.547474e-13   

           Gaze_Y  
252  1.136868e-13  
252  1.136868e-13  
252  1.136868e-13  
252  1.136868e-13  
252  1.136868e-13  
252  1.136868e-13  
      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_X  Right_Gaze_Y        Gaze_X  \
253  1.110223e-16  2.775558e-17  5.551115e-17  5.551115e-17  2.273737e-13   
253  1.110223e-16  2.775558e-17  5.551115e-17  5.551115e-17  2.273737e-13   
253  1.110223e-16  2.775558e-17  5.551115e-17  5.551115e-17  2.273737e-13   
253  1.11022

      Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
288  8.326673e-17  5.551115e-17  1.136868e-13
288  8.326673e-17  5.551115e-17  1.136868e-13
288  8.326673e-17  5.551115e-17  1.136868e-13
     Right_Gaze_X
289  1.110223e-16
      Left_Gaze_Y  Right_Gaze_X  Right_Gaze_Y
290  2.775558e-17 -5.551115e-17 -2.775558e-17
290  2.775558e-17 -5.551115e-17 -2.775558e-17
290  2.775558e-17 -5.551115e-17 -2.775558e-17
      Left_Gaze_Y  Right_Gaze_X  Right_Gaze_Y        Gaze_Y
291  2.775558e-17  5.551115e-17  5.551115e-17  5.684342e-14
291  2.775558e-17  5.551115e-17  5.551115e-17  5.684342e-14
291  2.775558e-17  5.551115e-17  5.551115e-17  5.684342e-14
291  2.775558e-17  5.551115e-17  5.551115e-17  5.684342e-14
      Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
292  5.551115e-17  2.775558e-17  5.684342e-14
292  5.551115e-17  2.775558e-17  5.684342e-14
292  5.551115e-17  2.775558e-17  5.684342e-14
      Left_Gaze_Y
293  2.775558e-17
      Left_Gaze_X   Left_Gaze_Y        Gaze_Y
294  5.551115e-17  5.551115e-1

      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
328  1.110223e-16  2.775558e-17  5.551115e-17  5.684342e-14
328  1.110223e-16  2.775558e-17  5.551115e-17  5.684342e-14
328  1.110223e-16  2.775558e-17  5.551115e-17  5.684342e-14
328  1.110223e-16  2.775558e-17  5.551115e-17  5.684342e-14
      Left_Gaze_Y  Right_Gaze_X  Right_Gaze_Y        Gaze_Y
329  5.551115e-17  5.551115e-17  2.775558e-17  1.136868e-13
329  5.551115e-17  5.551115e-17  2.775558e-17  1.136868e-13
329  5.551115e-17  5.551115e-17  2.775558e-17  1.136868e-13
329  5.551115e-17  5.551115e-17  2.775558e-17  1.136868e-13
      Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
331  8.326673e-17  2.775558e-17  1.136868e-13
331  8.326673e-17  2.775558e-17  1.136868e-13
331  8.326673e-17  2.775558e-17  1.136868e-13
      Left_Gaze_Y
332  2.775558e-17
      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
333  1.110223e-16  5.551115e-17  2.775558e-17  5.684342e-14
333  1.110223e-16  5.551115e-17  2.775558e-17  5.684342e-14


      Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
363  8.326673e-17 -2.775558e-17  1.136868e-13
363  8.326673e-17 -2.775558e-17  1.136868e-13
363  8.326673e-17 -2.775558e-17  1.136868e-13
      Left_Gaze_Y        Gaze_Y
364 -2.775558e-17 -5.684342e-14
364 -2.775558e-17 -5.684342e-14
      Left_Gaze_Y  Right_Gaze_X        Gaze_Y
365  5.551115e-17  5.551115e-17  5.684342e-14
365  5.551115e-17  5.551115e-17  5.684342e-14
365  5.551115e-17  5.551115e-17  5.684342e-14
      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_X  Right_Gaze_Y        Gaze_X  \
366  1.110223e-16  2.775558e-17  5.551115e-17  2.775558e-17  2.273737e-13   
366  1.110223e-16  2.775558e-17  5.551115e-17  2.775558e-17  2.273737e-13   
366  1.110223e-16  2.775558e-17  5.551115e-17  2.775558e-17  2.273737e-13   
366  1.110223e-16  2.775558e-17  5.551115e-17  2.775558e-17  2.273737e-13   
366  1.110223e-16  2.775558e-17  5.551115e-17  2.775558e-17  2.273737e-13   
366  1.110223e-16  2.775558e-17  5.551115e-17  2.775558e-17  2.273737e-13 

     Right_Gaze_Y        Gaze_Y
404  5.551115e-17  5.684342e-14
404  5.551115e-17  5.684342e-14
      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_X  Right_Gaze_Y        Gaze_X  \
405  5.551115e-17  5.551115e-17  5.551115e-17  2.775558e-17  2.273737e-13   
405  5.551115e-17  5.551115e-17  5.551115e-17  2.775558e-17  2.273737e-13   
405  5.551115e-17  5.551115e-17  5.551115e-17  2.775558e-17  2.273737e-13   
405  5.551115e-17  5.551115e-17  5.551115e-17  2.775558e-17  2.273737e-13   
405  5.551115e-17  5.551115e-17  5.551115e-17  2.775558e-17  2.273737e-13   
405  5.551115e-17  5.551115e-17  5.551115e-17  2.775558e-17  2.273737e-13   

           Gaze_Y  
405  5.684342e-14  
405  5.684342e-14  
405  5.684342e-14  
405  5.684342e-14  
405  5.684342e-14  
405  5.684342e-14  
      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
406 -5.551115e-17  8.326673e-17  8.326673e-17  1.136868e-13
406 -5.551115e-17  8.326673e-17  8.326673e-17  1.136868e-13
406 -5.551115e-17  8.326673e-17  8.326673e-1

      Left_Gaze_Y  Right_Gaze_Y        Gaze_Y
440  1.110223e-16  2.775558e-17  1.136868e-13
440  1.110223e-16  2.775558e-17  1.136868e-13
440  1.110223e-16  2.775558e-17  1.136868e-13
      Left_Gaze_X   Left_Gaze_Y  Right_Gaze_X        Gaze_X        Gaze_Y
441  1.110223e-16  5.551115e-17  5.551115e-17  2.273737e-13  5.684342e-14
441  1.110223e-16  5.551115e-17  5.551115e-17  2.273737e-13  5.684342e-14
441  1.110223e-16  5.551115e-17  5.551115e-17  2.273737e-13  5.684342e-14
441  1.110223e-16  5.551115e-17  5.551115e-17  2.273737e-13  5.684342e-14
441  1.110223e-16  5.551115e-17  5.551115e-17  2.273737e-13  5.684342e-14
      Left_Gaze_X  Right_Gaze_X  Right_Gaze_Y        Gaze_X        Gaze_Y
442  1.110223e-16  5.551115e-17  5.551115e-17  2.273737e-13  5.684342e-14
442  1.110223e-16  5.551115e-17  5.551115e-17  2.273737e-13  5.684342e-14
442  1.110223e-16  5.551115e-17  5.551115e-17  2.273737e-13  5.684342e-14
442  1.110223e-16  5.551115e-17  5.551115e-17  2.273737e-13  5.684342e-14
44

KeyboardInterrupt: 